In [1]:
import torch
from torch import nn
import numpy as np
import pandas as pd
import torch.nn.functional as F
import copy
import math
import os
from datetime import datetime

In [2]:
if torch.cuda.is_available():
    dev = "cuda:0"
else:
    dev = "cpu"

device = torch.device(dev)

In [3]:
class Embedder(nn.Module):
    def __init__(self, vocab_size, d_model):
        super().__init__()
        self.embed = nn.Embedding(vocab_size, d_model).cuda()
    
    def forward(self, x):
        return self.embed(x)

In [4]:
class PositionalEncoder(nn.Module):
    def __init__(self, d_model, max_seq_len = 200, dropout = 0.1):
        super().__init__()
        self.d_model = d_model
        self.dropout = nn.Dropout(dropout)
        pe = torch.zeros(max_seq_len, d_model)
        for pos in range(max_seq_len):
            for i in range(0, d_model, 2):
                pe[pos, i] = \
                math.sin(pos / (10000 ** ((2 * i)/d_model)))
                pe[pos, i + 1] = \
                math.cos(pos / (10000 ** ((2 * (i + 1))/d_model)))
        pe = pe.unsqueeze(0)
        self.register_buffer('pe', pe)
 
    def forward(self, x):
        x = x * math.sqrt(self.d_model)
        seq_len = x.size(1)
        pe = Variable(self.pe[:,:seq_len], requires_grad=False)
        if x.is_cuda:
            pe.cuda()
        x = x + pe
        return self.dropout(x)

In [5]:
class MultiHeadAttention(nn.Module):
    def __init__(self, heads, d_model, dropout = 0.1):
        super().__init__()
        self.d_model = d_model
        self.d_k = d_model // heads
        self.h = heads
        self.q_linear = nn.Linear(d_model, d_model).cuda()
        self.k_linear = nn.Linear(d_model, d_model).cuda()
        self.v_linear = nn.Linear(d_model, d_model).cuda()
        self.dropout = nn.Dropout(dropout).cuda()
        self.out = nn.Linear(d_model, d_model).cuda()
    
    def attention(self, q, k, v, d_k, mask = None, dropout = None):
        scores = torch.matmul(q, k.transpose(-2, -1))/math.sqrt(d_k)
        if mask is not None:
            mask = mask.unsqueeze(1)
#             print("scores.shape : {}".format(scores.shape))
#             print("mask.shape : {}".format(mask.shape))
            scores = scores.masked_fill(mask, -1e9)
        scores = F.softmax(scores, dim = -1)
#         if(scores.shape[2] != v.shape[2] or scores.shape[3] != v.shape[2]):
#             scores = scores[:, :, :v.shape[2], :v.shape[2]]
        if dropout is not None:
            scores = dropout(scores)
#         print("scores.shape : {}".format(scores.shape))
#         print("v.shape : {}".format(v.shape))
        output = torch.matmul(scores, v)
        return output
    
    def forward(self, q, k, v, mask = None):
        bs = q.size(0)
#         print("bs : {}".format(bs))
        q = self.q_linear(q).view(bs, -1, self.h, self.d_k)
        k = self.k_linear(k).view(bs, -1, self.h, self.d_k)
        v = self.v_linear(v).view(bs, -1, self.h, self.d_k)
#         print("q.shape : {} || k.shape : {} || v.shape : {}".format(q.shape, k.shape, v.shape))
        q = q.transpose(1,2)
        k = k.transpose(1,2)
        v = v.transpose(1,2)
#         print("q.shape : {} || k.shape : {} || v.shape : {}".format(q.shape, k.shape, v.shape))
        scores = self.attention(q, k, v, self.d_k, mask, self.dropout)
#         print("scores.shape : {}".format(scores.shape))
        concat = scores.transpose(1, 2).contiguous().view(bs, -1, self.d_model)
        output = self.out(concat)
        return output

In [6]:
class FeedForward(nn.Module):
    def __init__(self, d_model, d_ff=2048, dropout = 0.1):
        super().__init__() 
        # We set d_ff as a default to 2048
        self.linear_1 = nn.Linear(d_model, d_ff).cuda()
        self.dropout = nn.Dropout(dropout).cuda()
        self.linear_2 = nn.Linear(d_ff, d_model).cuda()
    
    def forward(self, x):
        x = self.dropout(F.relu(self.linear_1(x)).cuda())
        x = self.linear_2(x)
        return x

In [7]:
class Norm(nn.Module):
    def __init__(self, d_model, eps = 1e-6):
        super().__init__()
        self.size = d_model
        self.alpha = nn.Parameter(torch.ones(self.size).cuda()).cuda()
        self.bias = nn.Parameter(torch.zeros(self.size).cuda()).cuda()
        self.eps = eps
    
    def forward(self, x):
        norm = self.alpha * (x - x.mean(dim=-1, keepdim=True))/(x.std(dim=-1, keepdim=True) + self.eps) + self.bias
        return norm

In [8]:
class EncoderLayer(nn.Module):
    def __init__(self, d_model, heads, dropout = 0.1):
        super().__init__()
        self.norm1 = Norm(d_model).cuda()
        self.norm2 = Norm(d_model).cuda()
        self.attn = MultiHeadAttention(heads, d_model).cuda()
        self.ff = FeedForward(d_model).cuda()
        self.dropout1 = nn.Dropout(dropout).cuda()
        self.dropout2 = nn.Dropout(dropout).cuda()
    
    def forward(self, x, mask ):
#         print(x.shape)
        x1 = self.norm1(x)
#         print(x1.shape)
        temp = self.attn(x1, x1, x1, mask)
#         print(temp.shape)
        x = x + self.dropout1(temp)
        x2 = self.norm2(x)
        x = x + self.dropout2(self.ff(x2))
        return x

In [9]:
class DecoderLayer(nn.Module):
    def __init__(self, d_model, heads, dropout = 0.1):
        super().__init__()
        self.norm1 = Norm(d_model).cuda()
        self.norm2 = Norm(d_model).cuda()
        self.norm3 = Norm(d_model).cuda()
        self.dropout1 = nn.Dropout(dropout).cuda()
        self.dropout2 = nn.Dropout(dropout).cuda()
        self.dropout3 = nn.Dropout(dropout).cuda()
        self.attn1 = MultiHeadAttention(heads, d_model).cuda()
        self.attn2 = MultiHeadAttention(heads, d_model).cuda()
        self.ff = FeedForward(d_model).cuda()
    
    def forward(self, x, src_outputs, src_mask, tgt_mask):
        x1 = self.norm1(x)
        x = x + self.dropout1(self.attn1(x1, x1, x1, tgt_mask))
        x2 = self.norm2(x)
        x = x + self.dropout2(self.attn2(x2, src_outputs, src_outputs, src_mask))
        x3 = self.norm3(x)
        x = x + self.dropout3(self.ff(x3))
        return x

In [10]:
def getClones(module, N):
    return nn.ModuleList([copy.deepcopy(module) for i in range(N)])

In [11]:
class Encoder(nn.Module):
    def __init__(self, vocab_size, d_model, N, heads):
        super().__init__()
        self.N = N
        self.embed = Embedder(vocab_size, d_model).cuda()
        self.pe = PositionalEncoder(d_model).cuda()
        self.layers = getClones(EncoderLayer(d_model, heads).cuda(), N)
        self.norm = Norm(d_model).cuda()
    
    def forward(self, src, mask):
        x = self.embed(src)
        x = self.pe(x)
        for i in range(self.N):
            x = self.layers[i](x, mask)
        return self.norm(x)

In [12]:
class Decoder(nn.Module):
    def __init__(self, vocab_size, d_model, N, heads):
        super().__init__()
        self.N = N
        self.embed = Embedder(vocab_size, d_model).cuda()
        self.pe = PositionalEncoder(d_model).cuda()
        self.layers = getClones(DecoderLayer(d_model, heads).cuda(), N)
        self.norm = Norm(d_model).cuda()
    
    def forward(self, tgt, src_outputs, src_mask, tgt_mask):
        x = self.embed(tgt)
        x = self.pe(x)
        for i in range(self.N):
            x = self.layers[i](x, src_outputs, src_mask, tgt_mask)
        return self.norm(x)

In [13]:
class architecture(nn.Module):
    def __init__(self, src_vocab, tgt_vocab, d_model, Ne1, Ne2, Nd1, heads):
        super().__init__()
        self.encoder1 = Encoder(src_vocab, d_model, Ne1, heads).cuda()
        self.encoder2 = Encoder(src_vocab, d_model, Ne2, heads).cuda()
        self.decoder1 = Decoder(tgt_vocab, d_model, Nd1, heads).cuda()
        self.out = nn.Linear(d_model, tgt_vocab).cuda()
    
    def forward(self, src1, src2, tgt, src_mask1, src_mask2, tgt_mask, src_mask3, index_list):
        src_outputs1 = self.encoder1(src1, src_mask1)
#         print("source 1 completed")
        src_outputs2 = self.encoder2(src2, src_mask2)
#         print("source 1 completed")
        src_ouputs = []
        for i, index in enumerate(index_list):
            if(index == -1):
                src_ouputs.append(torch.cat([src_outputs1[i], src_outputs2[i]]))
            else:
                src_ouputs.append(torch.cat([src_outputs1[i, :index], src_outputs2[i], src_outputs1[i, index:]]))
            src_ouputs[i] = src_ouputs[i][:src_outputs1.shape[1]]
        src_ouputs = torch.stack(src_ouputs).cuda()
#         print("sources stacking completed")
        tgt_output = self.decoder1(tgt, src_ouputs, src_mask3, tgt_mask)
#         print("target side completed")
        output = self.out(tgt_output)
        return output
    
    def encode1(self, src, src_mask):
        return self.encoder1(src, src_mask)
    
    def encode2(self, src, src_mask):
        return self.encoder2(src, src_mask)
    
    def decode(self, tgt, src_output, src_mask, tgt_mask):
        return self.decoder1(tgt, src_output, src_mask, tgt_mask)
    
    def linearVocab(self, out):
        return self.out(out)

In [14]:
src_data = open("train.src").read().strip().split('\n')
tgt_data = open("train.tgt").read().strip().split('\n')
joint_vocab_freq = {}
for data in src_data:
    tokens = data.split(" ")
    for token in tokens:
        if token in joint_vocab_freq.keys():
            joint_vocab_freq[token] = joint_vocab_freq[token] + 1
        else:
            joint_vocab_freq[token] = 1
for data in tgt_data:
    tokens = data.split(" ")
    for token in tokens:
        if token in joint_vocab_freq.keys():
            joint_vocab_freq[token] = joint_vocab_freq[token] + 1
        else:
            joint_vocab_freq[token] = 1
sorted_joint_vocab_freq = sorted(joint_vocab_freq.items(), key=lambda x:x[1], reverse=True)
sorted_joint_vocab_freq = dict(sorted_joint_vocab_freq)
joint_vocab = list(sorted_joint_vocab_freq.keys())
joint_vocab.insert(0, "<END>")
joint_vocab.insert(0, "<START>")
joint_vocab.insert(0, "<PAD>")
joint_vocab.insert(0, "<UNK>")
#print(sorted_joint_vocab_freq)

In [15]:
print(joint_vocab)

['<UNK>', '<PAD>', '<START>', '<END>', '+', 'iti', 'api', 'eva', 'ca', 'a@@', 'na', 'ya@@', 'A@@', 'ma@@', 'M_@@', 'yA@@', 'vi@@', 'ka@@', 'mA@@', 'ra@@', 'pra@@', 'H', 'va@@', 'r@@', 'M', 'ya', 'yam', 'tu', 'ta@@', 't@@', 'e', 'vA@@', 'e@@', 'sva@@', 'sa@@', 's@@', 'yaH', 'm', 'kA@@', 'tat@@', 'nA@@', ':', 'asya', 'rA@@', 'na@@', 'an@@', 'saH', 'ni@@', 'o_@@', 'da@@', 'pa@@', 'la@@', 'yat', 'd@@', 'Sca', 'a', 'S@@', 'aH', 'tat', 'saM@@', 'tad@@', 'yA', 'Sa@@', 'pA@@', 'A', 'as@@', 'kaH', 'am', 'Ba@@', 'vA', 'ti@@', 'm@@', 'kam', 'l@@', 'ga@@', 'I@@', 'mapi', 'meva', 'tA@@', '_@@', 'tam', 'sya', 'n@@', 'ena', 'sA@@', 'k@@', 'it@@', 'ram', 'upa@@', 'ja@@', 'anu@@', 'su@@', 'ana@@', 't', 'yat@@', 'u@@', 'dA@@', 'n', '', 'taH', 'ita@@', 'BAva@@', 'tatra', 'h@@', 'iva', 'miti', 'j@@', 'ye@@', 'yAm', 'i@@', 'D@@', 'p@@', 'mat@@', 'cA@@', 'R@@', 'man@@', 'ityarTaH', 'yAH', 'sa_@@', 'yaM', 'raH', 'Ra@@', 'An@@', 'Bi@@', 'sam@@', 'z@@', 'pari@@', 'lA@@', 'Adi@@', 'BA@@', 'di@@', 'o@@', 'asti',

In [16]:
from sklearn.model_selection import train_test_split

In [17]:
maskembed = Embedder(len(joint_vocab), 512)
joint_vocab_index_dict = {}
for index, word in enumerate(joint_vocab):
    joint_vocab_index_dict[word] = index

# all_data = zip(list_a, list_b)
non_test_src_data, test_src_data, non_test_tgt_data, test_tgt_data = train_test_split(src_data, tgt_data, test_size=0.2, shuffle=True)
train_src_data, valid_src_data, train_tgt_data, valid_tgt_data = train_test_split(non_test_src_data, non_test_tgt_data, test_size=0.2, shuffle=True)

In [18]:
print(joint_vocab_index_dict)

{'<UNK>': 0, '<PAD>': 1, '<START>': 2, '<END>': 3, '+': 4, 'iti': 5, 'api': 6, 'eva': 7, 'ca': 8, 'a@@': 9, 'na': 10, 'ya@@': 11, 'A@@': 12, 'ma@@': 13, 'M_@@': 14, 'yA@@': 15, 'vi@@': 16, 'ka@@': 17, 'mA@@': 18, 'ra@@': 19, 'pra@@': 20, 'H': 21, 'va@@': 22, 'r@@': 23, 'M': 24, 'ya': 25, 'yam': 26, 'tu': 27, 'ta@@': 28, 't@@': 29, 'e': 30, 'vA@@': 31, 'e@@': 32, 'sva@@': 33, 'sa@@': 34, 's@@': 35, 'yaH': 36, 'm': 37, 'kA@@': 38, 'tat@@': 39, 'nA@@': 40, ':': 41, 'asya': 42, 'rA@@': 43, 'na@@': 44, 'an@@': 45, 'saH': 46, 'ni@@': 47, 'o_@@': 48, 'da@@': 49, 'pa@@': 50, 'la@@': 51, 'yat': 52, 'd@@': 53, 'Sca': 54, 'a': 55, 'S@@': 56, 'aH': 57, 'tat': 58, 'saM@@': 59, 'tad@@': 60, 'yA': 61, 'Sa@@': 62, 'pA@@': 63, 'A': 64, 'as@@': 65, 'kaH': 66, 'am': 67, 'Ba@@': 68, 'vA': 69, 'ti@@': 70, 'm@@': 71, 'kam': 72, 'l@@': 73, 'ga@@': 74, 'I@@': 75, 'mapi': 76, 'meva': 77, 'tA@@': 78, '_@@': 79, 'tam': 80, 'sya': 81, 'n@@': 82, 'ena': 83, 'sA@@': 84, 'k@@': 85, 'it@@': 86, 'ram': 87, 'upa@@': 88

In [19]:
def transformWords(name, joint_vocab_index_dict, src_data, tgt_data):
    with open("transformed/" + name + "_transformed_src.txt", "w") as fwritesrc, open("transformed/" + name+"_transformed_tgt.txt", "w") as fwritetgt:
        updated_src_data = []
        updated_tgt_data = []
        tgt_writing_content = ""
        for index1, line in enumerate(tgt_data):
            updated_tgt_data.append("<START>" + " " + line + " " + "<END>")
            updated_tgt_data[index1] = updated_tgt_data[index1].split(" ")
            tgt_writing_content = str(updated_tgt_data[index1])
            for index2, element in enumerate(updated_tgt_data[index1]):
                if(updated_tgt_data[index1][index2] in joint_vocab_index_dict.keys()):
                    updated_tgt_data[index1][index2] = joint_vocab_index_dict[updated_tgt_data[index1][index2]]
                else:
                    updated_tgt_data[index1][index2] = joint_vocab_index_dict["<UNK>"]
            tgt_writing_content = tgt_writing_content + "||" + str(updated_tgt_data[index1]) + "\n"
            fwritetgt.write(tgt_writing_content)
#             updated_tgt_data[index1] = torch.Tensor(updated_tgt_data[index1])
        src_writing_content = ""
        for index1, line in enumerate(src_data):
            updated_src_data.append(line.split(" "))
            src_writing_content = str(updated_src_data[index1])
            for index2, element in enumerate(updated_src_data[index1]):
                if(updated_src_data[index1][index2] in joint_vocab_index_dict.keys()):
                    updated_src_data[index1][index2] = joint_vocab_index_dict[updated_src_data[index1][index2]]
                else:
                    updated_src_data[index1][index2] = joint_vocab_index_dict["<UNK>"]
            src_writing_content = src_writing_content + "||" + str(updated_src_data[index1]) + "\n"
            fwritesrc.write(src_writing_content)
#             updated_src_data[index1] = torch.Tensor(updated_src_data[index1])
        return updated_src_data, updated_tgt_data

In [20]:
train_src_data, train_tgt_data = transformWords("train", joint_vocab_index_dict, train_src_data, train_tgt_data)
test_src_data, test_tgt_data = transformWords("test", joint_vocab_index_dict, test_src_data, test_tgt_data)
valid_src_data, valid_tgt_data = transformWords("valid", joint_vocab_index_dict, valid_src_data, valid_tgt_data)

In [21]:
train_df = pd.DataFrame({'src': train_src_data, 'tgt': train_tgt_data})
test_df = pd.DataFrame({'src': test_src_data, 'tgt': test_tgt_data})
valid_df = pd.DataFrame({'src': valid_src_data, 'tgt': valid_tgt_data})

In [22]:
train_df.to_csv("train_data.csv", index=False)
test_df.to_csv("test_data.csv", index=False)
valid_df.to_csv("valid_data.csv", index=False)

In [23]:
from torch.utils.data import Dataset, DataLoader
import ast
from torch.nn.utils.rnn import pad_sequence
import time 
from torch.autograd import Variable

In [24]:
class customDataset(Dataset):
    def __init__(self, csv_file):
        self.content = pd.read_csv(csv_file)
#         print(self.content['src'])
        self.content[['src1', 'src2']] = self.content['src'].str.split(', 4, ', expand=True)
#         self.content['src1'] = "[" + joint_vocab_index_dict["<START>"] + ", " + self.content['src1'].split("[")[1] + ", " + joint_vocab_index_dict["<END>"] + "]"
#         self.content['src2'] = "[" + joint_vocab_index_dict["<START>"] + ", " + self.content['src2'].split("]")[0] + ", " + joint_vocab_index_dict["<END>"] + "]"
        self.content['src1'] = self.content['src1'] + "]"
        self.content['src2'] = "[" + self.content['src2']
        self.source_texts1 = self.content['src1']
        self.source_texts2 = self.content['src2']
#         print(self.content['src1'])
#         print(self.content['src2'])
        self.target_texts = self.content['tgt']

    def __len__(self):
        return len(self.content)

    def __getitem__(self, idx):
#         print(type(self.content))
        src_data1 = ast.literal_eval(self.source_texts1[idx])
        src_data2 = ast.literal_eval(self.source_texts2[idx])
        tgt_data = ast.literal_eval(self.target_texts[idx])
#         print(src_data, tgt_data)
        return torch.tensor(src_data1).cuda(), torch.tensor(src_data2).cuda(), torch.tensor(tgt_data).cuda()

In [25]:
class MyCollate:
    def __init__(self, pad_idx):
        self.pad_idx = pad_idx
    
    def __call__(self, batch):
        batch_size = len(batch)
        source1 = [item[0] for item in batch]
#         source1 = pad_sequence(source1, batch_first=False, padding_value = self.pad_idx)
#         source1 = embed(source1)
        source2 = [item[1] for item in batch]
#         source2 = pad_sequence(source2, batch_first=False, padding_value = self.pad_idx)
#         source2 = embed(source2)    
        target = [item[2] for item in batch] 
#         target = pad_sequence(target, batch_first=False, padding_value = self.pad_idx)
        final = source1 + source2 + target
        #pad them using pad_sequence method from pytorch. 
        final = pad_sequence(final, batch_first=False, padding_value = self.pad_idx)
#         print(final.shape)
        source1 = final[:, :batch_size]
        source2 = final[:, batch_size:(2*batch_size)]
        target = final[:, (2*batch_size):(3*batch_size)]
#         target = embed(target)
        return source1, source2, target

In [26]:
class MyCollate1:
    def __init__(self, pad_idx):
        self.pad_idx = pad_idx
    
    def __call__(self, batch):
        source1 = [item[0] for item in batch]
        source1 = pad_sequence(source1, batch_first=False, padding_value = self.pad_idx)
#         source1 = embed(source1)
        source2 = [item[1] for item in batch]
        source2 = pad_sequence(source2, batch_first=False, padding_value = self.pad_idx)
#         source2 = embed(source2)    
        target = [item[2] for item in batch] 
        #pad them using pad_sequence method from pytorch. 
        target = pad_sequence(target, batch_first=False, padding_value = self.pad_idx)
#         target = embed(target)
        return source1, source2, target

In [27]:
def get_train_loader(dataset, joint_vocab_index_dict, batch_size, num_workers=0, shuffle=True, pin_memory=True): #increase num_workers according to CPU
    pad_idx = joint_vocab_index_dict["<PAD>"]
    loader = DataLoader(dataset, batch_size = batch_size, num_workers = num_workers,
                        shuffle=shuffle, pin_memory=pin_memory, collate_fn = MyCollate(pad_idx=pad_idx)) #MyCollate class runs __call__ method by default
    return loader

def get_valid_loader(dataset, joint_vocab_index_dict, batch_size, num_workers=0, shuffle=True, pin_memory=True):
    pad_idx = joint_vocab_index_dict["<PAD>"]
    loader = DataLoader(dataset, batch_size = batch_size, num_workers = num_workers,
                        shuffle=shuffle, pin_memory=pin_memory, collate_fn = MyCollate(pad_idx=pad_idx))
    return loader

In [28]:
# def get_train_loader1(dataset, joint_vocab_index_dict, batch_size, num_workers=0, shuffle=True, pin_memory=True): #increase num_workers according to CPU
#     pad_idx = joint_vocab_index_dict["<PAD>"]
#     loader = DataLoader(dataset, batch_size = batch_size, num_workers = num_workers,
#                         shuffle=shuffle, pin_memory=pin_memory, collate_fn = MyCollate1(pad_idx=pad_idx)) #MyCollate class runs __call__ method by default
#     return loader

In [29]:
train_dataset = customDataset("train_data.csv")
test_dataset = customDataset("test_data.csv")
valid_dataset = customDataset("valid_data.csv")

In [30]:
print(len(valid_dataset))

13160


In [31]:
train_tuple = zip(train_src_data, train_tgt_data)
test_tuple = zip(test_src_data, test_tgt_data)
valid_tuple = zip(valid_src_data, valid_tgt_data)

In [32]:
train_dataloader = get_train_loader(train_dataset, joint_vocab_index_dict, batch_size = 256, shuffle = True, pin_memory=False)

In [33]:
valid_dataloader = get_valid_loader(valid_dataset, joint_vocab_index_dict, batch_size = 256, shuffle = True, pin_memory=False)
test_dataloader = get_valid_loader(test_dataset, joint_vocab_index_dict, batch_size = 256, shuffle = True, pin_memory=False)

In [34]:
# train_dataloader1 = get_train_loader1(train_dataset, joint_vocab_index_dict, batch_size = 256, shuffle = True)|

In [35]:
# for i, (x1, x2, y) in enumerate(train_dataloader1):
#     print("{} || {} || {}".format(x1.shape, x2.shape, y.shape))

In [36]:
# for i, (x1, x2, y) in enumerate(train_dataloader):
#     print("{} || {} || {}".format(x1.shape, x2.shape, y.shape))

In [37]:
def getMasks(src1 = None, src2 = None, src = None , tgt = None):
    src_mask1 = None
    if(src1 is not None):
        src_mask1_1 = (src1 != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0
        src_mask1_2 = src_mask1_1.transpose(-2, -1)
        src_mask1 = ~torch.matmul(src_mask1_2, src_mask1_1).type(torch.bool).cuda()
    
    src_mask2 = None
    if(src2 is not None):
        src_mask2_1 = (src2 != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0
        src_mask2_2 = src_mask2_1.transpose(-2, -1)
        src_mask2 = ~torch.matmul(src_mask2_2, src_mask2_1).type(torch.bool).cuda()
    
    tgt_mask1 = None
    if(tgt is not None):
        tgt_mask1_1 = (tgt != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0
        tgt_mask1_2 = tgt_mask1_1.transpose(-2, -1)
        tgt_mask1 = ~torch.matmul(tgt_mask1_2, tgt_mask1_1).type(torch.bool)
        np_mask = np.triu(np.ones((tgt.size(0), tgt.size(1), tgt.size(1))), k=1).astype('uint8')
        np_mask =  Variable(torch.from_numpy(np_mask) == 1).cuda()
        tgt_mask1 = tgt_mask1 | np_mask
    
    src_mask3 = None
    if(src is not None and tgt is not None):
        src_mask3_1 = (src != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0
        src_mask3_2 = ((tgt != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0).transpose(-2, -1)
        src_mask3 = ~torch.matmul(src_mask3_2, src_mask3_1).type(torch.bool).cuda()
        for i in range(src_mask3.size(0)):
            for j in range(src_mask3.size(1)):
                for k in range(src_mask3.size(2)):
                    if(abs(j-k) > 1):
                        src_mask3[i][j][k] = True
    return src_mask1, src_mask2, tgt_mask1, src_mask3

In [38]:
src1, src2, tgt = next(iter(valid_dataloader))
src1 = src1.transpose(0, 1).cuda()
src2 = src2.transpose(0, 1).cuda()
tgt = tgt.transpose(0, 1).cuda()
print("src1.shape : {}".format(src1.shape))
print("src2.shape : {}".format(src2.shape))
print("tgt.shape : {}".format(tgt.shape))
print("tgt[0][0] : {}".format(type(tgt[0][0])))
print("tgt[0][0] : {}".format(tgt[0][0]))
tgt_input = tgt[:, :-1].cuda()
start_token = torch.from_numpy(np.array([joint_vocab_index_dict["<START>"]])).cuda()
src = []
index_list = []
tgt_list = []
for i in range(src1.size(0)):
    indexes = (src1[i] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
    if(indexes.shape[0] == 0):
        index_list.append(-1)
        src.append(torch.cat([src1[i], src2[i]]))
    else:
        index = indexes[0][0]
        index_list.append(index)
        src.append(torch.cat([src1[i, :index], src2[i], src1[i, index:]]))
    src[i] = src[i][:src1.size(1)]
    tgt_list.append(torch.cat([start_token, tgt_input[i, :]]).cuda())
src = torch.stack(src).cuda()
tgt_list_input = torch.stack(tgt_list).cuda()
src_mask1, src_mask2, _, src_mask3 = getMasks(src1, src2, src, tgt_input)
print(src_mask1.shape)
print(src_mask2.shape)
print(src_mask3.shape)

src1.shape : torch.Size([256, 17])
src2.shape : torch.Size([256, 17])
tgt.shape : torch.Size([256, 17])
tgt[0][0] : <class 'torch.Tensor'>
tgt[0][0] : 2
torch.Size([256, 17, 17])
torch.Size([256, 17, 17])
torch.Size([256, 16, 17])


In [39]:
def prediction_loss_old(model, dataloader):
    model.eval()
    with torch.no_grad():
        total_loss = 0
        counter = 0
        for i, (src1, src2, tgt) in enumerate(dataloader):
            src1 = src1.transpose(0, 1).cuda()
            src2 = src2.transpose(0, 1).cuda()
            tgt = tgt.transpose(0, 1).cuda()
            tgt_input = tgt[:, :-1].cuda()
            start_token = torch.from_numpy(np.array([joint_vocab_index_dict["<START>"]])).cuda()
            src = []
            index_list = []
            tgt_list = []
            for i in range(src1.size(0)):
                indexes = (src1[i] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
                if(indexes.shape[0] == 0):
                    index_list.append(-1)
                    src.append(torch.cat([src1[i], src2[i]]))
                else:
                    index = indexes[0][0]
                    index_list.append(index)
                    src.append(torch.cat([src1[i, :index], src2[i], src1[i, index:]]))
                src[i] = src[i][:src1.size(1)]
                tgt_list.append(torch.cat([start_token, tgt_input[i, :]]).cuda())
            src = torch.stack(src).cuda()
            tgt_list_input = torch.stack(tgt_list).cuda()
            src_mask1, src_mask2, tgt_mask1, src_mask3 = getMasks(src1, src2, src, tgt_list_input)
            preds = model(src1, src2, tgt_list_input, src_mask1, src_mask2, tgt_mask1, src_mask3, index_list)
            ys = tgt[:, :].contiguous().view(-1)
            preds_just = preds.view(-1, preds.size(-1))
            loss = F.cross_entropy(preds_just, ys, ignore_index=joint_vocab_index_dict["<PAD>"])
            total_loss += loss.item()
            counter = counter + 1
        curr_loss = total_loss/counter
        return curr_loss

In [40]:
def prediction_loss(model, dataloader):
    model.eval()
    with torch.no_grad():
        total_loss = 0
        counter = 0
        for i, (src1, src2, tgt) in enumerate(dataloader):
            src1 = src1.transpose(0, 1).cuda()
            src2 = src2.transpose(0, 1).cuda()
            tgt = tgt.transpose(0, 1).cuda()
            tgt_input = tgt[:, :-1].cuda()
#             start_token = torch.from_numpy(np.array([joint_vocab_index_dict["<START>"]])).cuda()
            src = []
            index_list = []
#             tgt_list = []
            for i in range(src1.size(0)):
                indexes = (src1[i] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
                if(indexes.shape[0] == 0):
                    index_list.append(-1)
                    src.append(torch.cat([src1[i], src2[i]]))
                else:
                    index = indexes[0][0]
                    index_list.append(index)
                    src.append(torch.cat([src1[i, :index], src2[i], src1[i, index:]]))
                src[i] = src[i][:src1.size(1)]
#                 tgt_list.append(torch.cat([start_token, tgt_input[i, :]]).cuda())
            src = torch.stack(src).cuda()
#             tgt_list_input = torch.stack(tgt_list).cuda()
            src_mask1, src_mask2, tgt_mask1, src_mask3 = getMasks(src1, src2, src, tgt_input)
            preds = model(src1, src2, tgt_input, src_mask1, src_mask2, tgt_mask1, src_mask3, index_list)
            ys = tgt[:, 1:].contiguous().view(-1)
            preds_just = preds.view(-1, preds.size(-1))
            loss = F.cross_entropy(preds_just, ys, ignore_index=joint_vocab_index_dict["<PAD>"])
            total_loss += loss.item()
            counter = counter + 1
        curr_loss = total_loss/counter
        return curr_loss

In [41]:
epochs = 50
lr = 0.00005
betas = (0.9, 0.98)
d_model = 512
Ne1 = 2
Ne2 = 2
Nd1 = 2
heads = 1
checkpoint = 2

In [42]:
model = architecture(src_vocab=len(joint_vocab), tgt_vocab=len(joint_vocab), d_model=d_model, Ne1=Ne1, Ne2=Ne2, Nd1=Nd1, heads=heads)
model = model.cuda()
optimizer = torch.optim.Adam(model.parameters(), lr=lr, betas=betas, eps=1e-9)

In [43]:
model.train()

architecture(
  (encoder1): Encoder(
    (embed): Embedder(
      (embed): Embedding(5092, 512)
    )
    (pe): PositionalEncoder(
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (layers): ModuleList(
      (0): EncoderLayer(
        (norm1): Norm()
        (norm2): Norm()
        (attn): MultiHeadAttention(
          (q_linear): Linear(in_features=512, out_features=512, bias=True)
          (k_linear): Linear(in_features=512, out_features=512, bias=True)
          (v_linear): Linear(in_features=512, out_features=512, bias=True)
          (dropout): Dropout(p=0.1, inplace=False)
          (out): Linear(in_features=512, out_features=512, bias=True)
        )
        (ff): FeedForward(
          (linear_1): Linear(in_features=512, out_features=2048, bias=True)
          (dropout): Dropout(p=0.1, inplace=False)
          (linear_2): Linear(in_features=2048, out_features=512, bias=True)
        )
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, 

In [44]:
start = time.time()
current_datetime = datetime.now()
best_valid_data_loss = float('inf')
with open("logs/loss_log_"+str(current_datetime.year)+"_"+str(current_datetime.month)+"_"+str(current_datetime.day)+"_"+str(current_datetime.hour)+"_"+str(current_datetime.minute)+"_"+str(current_datetime.second)+".log", "w") as flogwrite:
    for epoch in range(epochs):
        model.train()
        total_loss = 0
        counter = 0
        for i, (src1, src2, tgt) in enumerate(valid_dataloader):
            src1 = src1.transpose(0, 1).cuda()
            src2 = src2.transpose(0, 1).cuda()
            tgt = tgt.transpose(0, 1).cuda()
            tgt_input = tgt[:, :-1].cuda()
#             print("src1[0] : {}".format(src1[0]))
#             print("src2[0] : {}".format(src2[0]))
#             print("tgt_input[0] : {}".format(tgt_input[0]))
#             print("src1.shape : {}".format(src1.shape))
#             print("src2.shape : {}".format(src2.shape))
#             print("tgt_input.shape : {}".format(tgt_input.shape))
#             start_token = torch.from_numpy(np.array([joint_vocab_index_dict["<START>"]])).cuda()
            src = []
            index_list = []
            tgt_list = []
            for i in range(src1.size(0)):
                indexes = (src1[i] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
                if(indexes.shape[0] == 0):
                    index_list.append(-1)
                    src.append(torch.cat([src1[i], src2[i]]))
                else:
                    index = indexes[0][0]
                    index_list.append(index)
                    src.append(torch.cat([src1[i, :index], src2[i], src1[i, index:]]))
                src[i] = src[i][:src1.size(1)]
#                 tgt_list.append(torch.cat([start_token, tgt_input[i, :]]))
            src = torch.stack(src).cuda()
#             tgt_list_input = torch.stack(tgt_list).cuda()
            src_mask1, src_mask2, tgt_mask1, src_mask3 = getMasks(src1, src2, src, tgt_input)
#             src1 = src1.type(torch.LongTensor)
#             src2 = src2.type(torch.LongTensor)
#             tgt = tgt.type(torch.LongTensor)
#             print("tgt_list_input.shape : {}".format(tgt_list_input.shape))
#             print("src.shape : {}".format(src.shape))
#             print("tgt_mask1[0] : {}".format(tgt_mask1[0]))
#             print("src_mask1[0] : {}".format(src_mask1[0]))
#             print("src_mask2[0] : {}".format(src_mask2[0]))
#             print("src_mask3[0] : {}".format(src_mask3[0]))
            preds = model(src1, src2, tgt_input, src_mask1, src_mask2, tgt_mask1, src_mask3, index_list)
#             print("preds.shape : {}".format(preds.shape))
            ys = tgt[:, 1:].contiguous().view(-1)
            preds_just = preds.view(-1, preds.size(-1))
#             print("preds_just.shape : {}".format(preds_just.shape))
#             print("ys.shape : {}".format(ys.shape))
            optimizer.zero_grad()
            loss = F.cross_entropy(preds_just, ys, ignore_index=joint_vocab_index_dict["<PAD>"])
            loss.backward()
            optimizer.step()
            total_loss += loss.item()
            counter = counter + 1
            print("total time till : {} || epoch : {} || batch : {} || train loss : {}".format((time.time() - start)//60, epoch + 1, counter, loss.item()))
            flogwrite.write("total time till : {} || epoch : {} || batch : {} || train loss : {}\n".format((time.time() - start)//60, epoch + 1, counter, loss.item()))
        curr_valid_data_loss = prediction_loss(model, valid_dataloader)
        if(curr_valid_data_loss < best_valid_data_loss):
            torch.save(model.state_dict(), 'checkpoints/best_checkpoint.pt')
            best_valid_data_loss = curr_valid_data_loss
        if(epoch == 0):
            torch.save(model.state_dict(), 'checkpoints/'+str(epoch+1)+'.pt')
        else:
            os.remove("checkpoints/"+str(epoch)+".pt")
            torch.save(model.state_dict(), 'checkpoints/'+str(epoch+1)+'.pt')
        print("total time till : {} || epoch : {} || train loss : {} || valid loss : {}".format((time.time() - start)//60, epoch + 1, total_loss/counter, curr_valid_data_loss))
        flogwrite.write("total time till : {} || epoch : {} || train loss : {} || valid loss : {}\n".format((time.time() - start)//60, epoch + 1, total_loss/counter, curr_valid_data_loss))

total time till : 0.0 || epoch : 1 || batch : 1 || train loss : 8.701258659362793
total time till : 0.0 || epoch : 1 || batch : 2 || train loss : 8.710423469543457
total time till : 0.0 || epoch : 1 || batch : 3 || train loss : 8.678816795349121
total time till : 0.0 || epoch : 1 || batch : 4 || train loss : 8.667893409729004
total time till : 0.0 || epoch : 1 || batch : 5 || train loss : 8.684704780578613
total time till : 0.0 || epoch : 1 || batch : 6 || train loss : 8.643802642822266
total time till : 0.0 || epoch : 1 || batch : 7 || train loss : 8.659290313720703
total time till : 0.0 || epoch : 1 || batch : 8 || train loss : 8.635480880737305
total time till : 0.0 || epoch : 1 || batch : 9 || train loss : 8.639678955078125
total time till : 0.0 || epoch : 1 || batch : 10 || train loss : 8.61617660522461
total time till : 0.0 || epoch : 1 || batch : 11 || train loss : 8.593066215515137
total time till : 0.0 || epoch : 1 || batch : 12 || train loss : 8.640117645263672
total time til

total time till : 2.0 || epoch : 2 || batch : 47 || train loss : 7.040359973907471
total time till : 2.0 || epoch : 2 || batch : 48 || train loss : 6.99198055267334
total time till : 2.0 || epoch : 2 || batch : 49 || train loss : 7.0012712478637695
total time till : 2.0 || epoch : 2 || batch : 50 || train loss : 7.019412040710449
total time till : 2.0 || epoch : 2 || batch : 51 || train loss : 6.958769798278809
total time till : 2.0 || epoch : 2 || batch : 52 || train loss : 6.9433159828186035
total time till : 3.0 || epoch : 2 || train loss : 7.331162351828355 || valid loss : 6.906255181019123
total time till : 3.0 || epoch : 3 || batch : 1 || train loss : 6.945932388305664
total time till : 3.0 || epoch : 3 || batch : 2 || train loss : 6.858041286468506
total time till : 3.0 || epoch : 3 || batch : 3 || train loss : 6.904875755310059
total time till : 3.0 || epoch : 3 || batch : 4 || train loss : 6.97139310836792
total time till : 3.0 || epoch : 3 || batch : 5 || train loss : 6.86198

total time till : 5.0 || epoch : 4 || batch : 40 || train loss : 6.448262691497803
total time till : 5.0 || epoch : 4 || batch : 41 || train loss : 6.516315460205078
total time till : 5.0 || epoch : 4 || batch : 42 || train loss : 6.474239826202393
total time till : 5.0 || epoch : 4 || batch : 43 || train loss : 6.519841194152832
total time till : 5.0 || epoch : 4 || batch : 44 || train loss : 6.515661716461182
total time till : 5.0 || epoch : 4 || batch : 45 || train loss : 6.473293781280518
total time till : 5.0 || epoch : 4 || batch : 46 || train loss : 6.496285915374756
total time till : 5.0 || epoch : 4 || batch : 47 || train loss : 6.552820205688477
total time till : 5.0 || epoch : 4 || batch : 48 || train loss : 6.428344249725342
total time till : 5.0 || epoch : 4 || batch : 49 || train loss : 6.467967510223389
total time till : 5.0 || epoch : 4 || batch : 50 || train loss : 6.491813659667969
total time till : 5.0 || epoch : 4 || batch : 51 || train loss : 6.414359092712402
tota

total time till : 7.0 || epoch : 6 || batch : 33 || train loss : 6.311065673828125
total time till : 7.0 || epoch : 6 || batch : 34 || train loss : 6.228540897369385
total time till : 7.0 || epoch : 6 || batch : 35 || train loss : 6.195413112640381
total time till : 8.0 || epoch : 6 || batch : 36 || train loss : 6.317757606506348
total time till : 8.0 || epoch : 6 || batch : 37 || train loss : 6.301297664642334
total time till : 8.0 || epoch : 6 || batch : 38 || train loss : 6.300343990325928
total time till : 8.0 || epoch : 6 || batch : 39 || train loss : 6.296855449676514
total time till : 8.0 || epoch : 6 || batch : 40 || train loss : 6.316158771514893
total time till : 8.0 || epoch : 6 || batch : 41 || train loss : 6.316064834594727
total time till : 8.0 || epoch : 6 || batch : 42 || train loss : 6.3233561515808105
total time till : 8.0 || epoch : 6 || batch : 43 || train loss : 6.250950813293457
total time till : 8.0 || epoch : 6 || batch : 44 || train loss : 6.300443172454834
tot

total time till : 10.0 || epoch : 8 || batch : 26 || train loss : 6.036102294921875
total time till : 11.0 || epoch : 8 || batch : 27 || train loss : 6.155474662780762
total time till : 11.0 || epoch : 8 || batch : 28 || train loss : 6.199141979217529
total time till : 11.0 || epoch : 8 || batch : 29 || train loss : 6.110373497009277
total time till : 11.0 || epoch : 8 || batch : 30 || train loss : 6.174281120300293
total time till : 11.0 || epoch : 8 || batch : 31 || train loss : 6.179749965667725
total time till : 11.0 || epoch : 8 || batch : 32 || train loss : 6.126157283782959
total time till : 11.0 || epoch : 8 || batch : 33 || train loss : 6.154359817504883
total time till : 11.0 || epoch : 8 || batch : 34 || train loss : 6.219833850860596
total time till : 11.0 || epoch : 8 || batch : 35 || train loss : 6.166901588439941
total time till : 11.0 || epoch : 8 || batch : 36 || train loss : 6.164201259613037
total time till : 11.0 || epoch : 8 || batch : 37 || train loss : 6.13466691

...

total time till : 62.0 || epoch : 43 || batch : 13 || train loss : 4.150684356689453
total time till : 62.0 || epoch : 43 || batch : 14 || train loss : 4.187222957611084
total time till : 62.0 || epoch : 43 || batch : 15 || train loss : 4.250659465789795
total time till : 62.0 || epoch : 43 || batch : 16 || train loss : 4.141616344451904
total time till : 62.0 || epoch : 43 || batch : 17 || train loss : 4.157297134399414
total time till : 62.0 || epoch : 43 || batch : 18 || train loss : 4.029686450958252
total time till : 62.0 || epoch : 43 || batch : 19 || train loss : 4.136040210723877
total time till : 62.0 || epoch : 43 || batch : 20 || train loss : 4.193331718444824
total time till : 62.0 || epoch : 43 || batch : 21 || train loss : 4.136740207672119
total time till : 62.0 || epoch : 43 || batch : 22 || train loss : 4.228785037994385
total time till : 62.0 || epoch : 43 || batch : 23 || train loss : 4.175119400024414
total time till : 63.0 || epoch : 43 || batch : 24 || train loss 

total time till : 65.0 || epoch : 45 || batch : 3 || train loss : 3.956312894821167
total time till : 65.0 || epoch : 45 || batch : 4 || train loss : 4.108011722564697
total time till : 65.0 || epoch : 45 || batch : 5 || train loss : 4.105432510375977
total time till : 65.0 || epoch : 45 || batch : 6 || train loss : 3.9904749393463135
total time till : 65.0 || epoch : 45 || batch : 7 || train loss : 4.040441036224365
total time till : 65.0 || epoch : 45 || batch : 8 || train loss : 4.114285945892334
total time till : 65.0 || epoch : 45 || batch : 9 || train loss : 4.006240367889404
total time till : 65.0 || epoch : 45 || batch : 10 || train loss : 4.090666770935059
total time till : 65.0 || epoch : 45 || batch : 11 || train loss : 4.101981163024902
total time till : 65.0 || epoch : 45 || batch : 12 || train loss : 4.018230438232422
total time till : 65.0 || epoch : 45 || batch : 13 || train loss : 4.027148723602295
total time till : 65.0 || epoch : 45 || batch : 14 || train loss : 4.11

total time till : 67.0 || epoch : 46 || batch : 47 || train loss : 3.8567988872528076
total time till : 67.0 || epoch : 46 || batch : 48 || train loss : 3.9809112548828125
total time till : 67.0 || epoch : 46 || batch : 49 || train loss : 3.9635260105133057
total time till : 67.0 || epoch : 46 || batch : 50 || train loss : 3.919401168823242
total time till : 67.0 || epoch : 46 || batch : 51 || train loss : 3.9251468181610107
total time till : 67.0 || epoch : 46 || batch : 52 || train loss : 4.085432529449463
total time till : 68.0 || epoch : 46 || train loss : 3.983519054376162 || valid loss : 3.666189276255094
total time till : 68.0 || epoch : 47 || batch : 1 || train loss : 3.9357383251190186
total time till : 68.0 || epoch : 47 || batch : 2 || train loss : 3.95544695854187
total time till : 68.0 || epoch : 47 || batch : 3 || train loss : 3.946756601333618
total time till : 68.0 || epoch : 47 || batch : 4 || train loss : 3.9173543453216553
total time till : 68.0 || epoch : 47 || batc

total time till : 70.0 || epoch : 48 || batch : 37 || train loss : 3.8375046253204346
total time till : 70.0 || epoch : 48 || batch : 38 || train loss : 3.859886646270752
total time till : 70.0 || epoch : 48 || batch : 39 || train loss : 3.9002699851989746
total time till : 70.0 || epoch : 48 || batch : 40 || train loss : 3.878978967666626
total time till : 70.0 || epoch : 48 || batch : 41 || train loss : 3.82381010055542
total time till : 70.0 || epoch : 48 || batch : 42 || train loss : 3.7939453125
total time till : 70.0 || epoch : 48 || batch : 43 || train loss : 3.797196626663208
total time till : 70.0 || epoch : 48 || batch : 44 || train loss : 3.90925669670105
total time till : 70.0 || epoch : 48 || batch : 45 || train loss : 3.8996222019195557
total time till : 70.0 || epoch : 48 || batch : 46 || train loss : 3.7989237308502197
total time till : 70.0 || epoch : 48 || batch : 47 || train loss : 3.805739641189575
total time till : 70.0 || epoch : 48 || batch : 48 || train loss : 3

total time till : 73.0 || epoch : 50 || batch : 27 || train loss : 3.8242406845092773
total time till : 73.0 || epoch : 50 || batch : 28 || train loss : 3.7618958950042725
total time till : 73.0 || epoch : 50 || batch : 29 || train loss : 3.7805047035217285
total time till : 73.0 || epoch : 50 || batch : 30 || train loss : 3.7653257846832275
total time till : 73.0 || epoch : 50 || batch : 31 || train loss : 3.7895171642303467
total time till : 73.0 || epoch : 50 || batch : 32 || train loss : 3.718961238861084
total time till : 73.0 || epoch : 50 || batch : 33 || train loss : 3.684338092803955
total time till : 73.0 || epoch : 50 || batch : 34 || train loss : 3.6535451412200928
total time till : 73.0 || epoch : 50 || batch : 35 || train loss : 3.68745493888855
total time till : 73.0 || epoch : 50 || batch : 36 || train loss : 3.8325603008270264
total time till : 73.0 || epoch : 50 || batch : 37 || train loss : 3.722686529159546
total time till : 73.0 || epoch : 50 || batch : 38 || train

In [79]:
train_dataloader_inference = get_train_loader(train_dataset, joint_vocab_index_dict, batch_size = 1, shuffle = False, pin_memory=False)
valid_dataloader_inference = get_valid_loader(valid_dataset, joint_vocab_index_dict, batch_size = 1, shuffle = False, pin_memory=False)
test_dataloader_inference = get_valid_loader(test_dataset, joint_vocab_index_dict, batch_size = 1, shuffle = False, pin_memory=False)

In [80]:
def generate(model, src1, src2):
    model.eval()
    with torch.no_grad():
#         pad_token = torch.from_numpy(np.array([joint_vocab_index_dict["<PAD>"]])).cuda()
        num_tokens1 = src1.size(1)
        src1 = src1.cuda()
        num_tokens2 = src2.size(1)
        src2 = src2.cuda()
#         src_list1 = []
#         src_list2 = []
#         for i in range(src1.size(0)):
#             src_list1.append(torch.cat([src1[i, :], pad_token, pad_token, pad_token]))
#             src_list2.append(torch.cat([src2[i, :], pad_token, pad_token, pad_token]))
#         src_list_input1 = torch.stack(src_list1).cuda()
#         src_list_input2 = torch.stack(src_list2).cuda()
#         print("src_list_input1.shape : {}".format(src_list_input1.shape))
#         print("src_list_input2.shape : {}".format(src_list_input2.shape))
#         src = []
#         for i in range(src1.size(0)):
#             src.append(torch.cat([src_list_input1[i, :-3], src_list_input2[i , :-3], src_list_input1[i, -3:], src_list_input2[i, -3:]]))
#         src = torch.stack(src).cuda()
        src = []
        for i in range(src1.size(0)):
            src.append(torch.cat([src1[i], src2[i]]))
        src = torch.stack(src).cuda()
#         print("src.shape : {}".format(src.shape))
#         src_mask1, src_mask2, _, src_mask3 = getMasks(src1 = src_list_input1, src2 = src_list_input2, src = src)
        src_mask1, src_mask2, _, _ = getMasks(src1 = src1, src2 = src2)
#         print("src_mask1.shape : {}".format(src_mask1.shape))
#         print("src_mask2.shape : {}".format(src_mask2.shape))
#         print("src_mask3.shape : {}".format(src_mask3.shape))
#         src_output1 = model.encode1(src_list_input1, src_mask1)
#         src_output2 = model.encode2(src_list_input2, src_mask2)
        src_output1 = model.encode1(src1, src_mask1)
        src_output2 = model.encode2(src2, src_mask2)
        start_token = torch.stack([torch.from_numpy(np.array([joint_vocab_index_dict["<START>"]]))]).cuda()
        ys = start_token
#         print("ys.shape : {}".format(ys.shape))
        src_output = torch.stack([torch.cat([src_output1[0], src_output2[0]])]).cuda()
#         print("src_output1.shape : {}".format(src_output1.shape))
#         print("src_output2.shape : {}".format(src_output2.shape))
#         print("src_output.shape : {}".format(src_output.shape))
        for i in range(src_output.shape[1] + 6):
            _, _, tgt_mask, src_mask3 = getMasks(src1 = src1, src2 = src2, src = src, tgt = ys)
#             print("tgt_mask : {}".format(tgt_mask))
#             print("src_mask3 : {}".format(src_mask3))
#             src_mask3_1 = (src != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0
#             src_mask3_2 = ((tgt != joint_vocab_index_dict["<PAD>"]).unsqueeze(-2) + 0.0).transpose(-2, -1)
#             src_mask3 = ~torch.matmul(src_mask3_2, src_mask3_1).type(torch.bool).cuda()
#             for i in range(src_mask3.size(0)):
#                 for j in range(src_mask3.size(1)):
#                     for k in range(src_mask3.size(2)):
#                         if(abs(j-k) > 1):
#                             src_mask3[i][j][k] = True
#             tgt_mask = np.triu(np.ones((ys.shape[0], ys.shape[1], ys.shape[1])), k=1).astype('uint8')
#             tgt_mask = Variable(torch.from_numpy(tgt_mask) == 1).cuda()
#             print("tgt_mask.shape : {}".format(tgt_mask.shape))
            out = model.decode(ys, src_output, src_mask3, tgt_mask)
            out = model.linearVocab(out)
#             print("out.shape : {}".format(out.shape))
#             print("out : {}".format(out))
            probs = F.softmax(out, dim = -1)
#             print("probs : {}".format(probs))
#             print("probs.shape : {}".format(probs.shape))
#             print(torch.argmax(probs, dim=-1))
#             print(torch.argmax(probs[0], dim=-1))
#             print("torch.argmax(probs, dim=-1) : {}".format(torch.argmax(probs, dim=-1)))
#             print("torch.max(probs, dim=-1) : {}".format(torch.max(probs, dim=-1)))
            obtained_index = torch.argmax(probs, dim=-1)[:, -1:]
#             print(obtained_index.item())
            if(obtained_index.item() == joint_vocab_index_dict["<END>"]):
                return ys
            else:
                ys = torch.stack([torch.cat([ys[0, :], obtained_index[0, :]])]).cuda()
#                 print("ys : {}".format(ys))
#                 print("ys.shape : {}".format(ys.shape))
        return ys

In [81]:
def bpeDecode(src_word):
    src_word_string = ""
    flag = False
    for i in range(len(src_word)):
        if(src_word[i] == "<START>" or src_word[i] == "<END>" or src_word[i] == "<PAD>"):
            continue;
        else:
            if("@@" in src_word[i]):
                if(flag):
                    src_word_string = src_word_string + str(src_word[i].split("@@")[0])
                else:
                    src_word_string = src_word_string + " " + str(src_word[i].split("@@")[0])
                flag = True
            else:
                if(flag):
                    src_word_string = src_word_string + src_word[i]
                else:
                    src_word_string = src_word_string + " " + src_word[i]
                flag = False
    return src_word_string.strip()

In [82]:
def printWord(src1, src2, tgt, preds, data):
#     print(src1)
    src_word1 = []
    for i in range(src1.shape[0]):
        for j in range(src1.shape[1]):
            src_word1.append(list(filter(lambda x: joint_vocab_index_dict[x] == src1[i, j], joint_vocab_index_dict))[0])
    src_word2 = []
    for i in range(src2.shape[0]):
        for j in range(src2.shape[1]):
            src_word2.append(list(filter(lambda x: joint_vocab_index_dict[x] == src2[i, j], joint_vocab_index_dict))[0])
    tgt_word = []
    for i in range(tgt.shape[0]):
        for j in range(tgt.shape[1]):
            tgt_word.append(list(filter(lambda x: joint_vocab_index_dict[x] == tgt[i, j], joint_vocab_index_dict))[0])
    preds_word = []
    for i in range(preds.shape[0]):
        for j in range(preds.shape[1]):
            preds_word.append(list(filter(lambda x: joint_vocab_index_dict[x] == preds[i, j], joint_vocab_index_dict))[0])
    src_word = src_word1 + list("+") + src_word2
    src_word_string = bpeDecode(src_word)
    tgt_word_string = bpeDecode(tgt_word)
    preds_word_string = bpeDecode(preds_word)
    return src_word_string, tgt_word_string, preds_word_string
#     print("src_word :\t{}".format(src_word))
#     print("tgt_word :\t{}".format(tgt_word))
#     print("preds_word :\t{}".format(preds_word))
#     print("src_word :\t{}".format(src_word_string))
#     print("tgt_word :\t{}".format(tgt_word_string))
#     print("preds_word :\t{}".format(preds_word_string))

In [83]:
def inference(model, dataloader, data):
    model.eval()
    with open("output/" + str(data) + "_output.txt", "a") as fwrite:
        for i, (src1, src2, tgt) in enumerate(dataloader):
            src1 = src1.transpose(0, 1).cuda()
            src2 = src2.transpose(0, 1).cuda()
            indexes1 = (src1[0] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
            if(indexes1.shape[0] != 0):
                index1 = indexes1[0][0]
                src1 = src1[:, :index1]
    #         print("src1.shape : {}".format(src1.shape))
    #         print("src1 : {}".format(src1))
            indexes2 = (src2[0] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
            if(indexes2.shape[0] != 0):
                index2 = indexes2[0][0]
                src2 = src2[:, :index2]
    #         print("src2.shape : {}".format(src2.shape))
    #         print("src2 : {}".format(src2))
            tgt = tgt.transpose(0, 1).cuda()
            preds = generate(model, src1, src2)
            src_word_string, tgt_word_string, preds_word_string = printWord(src1, src2, tgt, preds, data)
            fwrite.write("src_word :\t{}\n".format(src_word_string))
            fwrite.write("tgt_word :\t{}\n".format(tgt_word_string))
            fwrite.write("preds_word :\t{}\n".format(preds_word_string))
            print("src_word :\t{}".format(src_word_string))
            print("tgt_word :\t{}".format(tgt_word_string))
            print("preds_word :\t{}".format(preds_word_string))

In [84]:
inference(model, test_dataloader_inference, "test")

src_word :	rahasyam + jYAsyasi
tgt_word :	rahasyaM_jYAsyasi
preds_word :	AhaM_smAt
src_word :	niSAgaman + ASaNkayA
tgt_word :	niSAgamanASaNkayA
preds_word :	svaputraM_prAptavAn
src_word :	militezu + asmAsu
tgt_word :	militezvasmAsu
preds_word :	tasyAnopasTitIyaM_kftvA
src_word :	vAtAyanam + Bak
tgt_word :	vAtAyanaM_Bak
preds_word :	svarUpAM_BaRat
src_word :	rakzitam + kuSapuzpakEH
tgt_word :	rakzitaM_kuSapuzpakEH
preds_word :	viSezaRamitirItyA
src_word :	iti + etAdfSa
tgt_word :	ityetAdfSa
preds_word :	ityapfcCat
src_word :	kAruRyam + Atanvate
tgt_word :	kAruRyamAtanvate
preds_word :	kAyadikazAe
src_word :	viSezaRam + itirItyA
tgt_word :	viSezaRamitirItyA
preds_word :	viSezaRamitirItyA
src_word :	jagat + idam
tgt_word :	jagadidam
preds_word :	idaM_tu
src_word :	tatra + ekA
tgt_word :	tatrEkA
preds_word :	tatrAM
src_word :	kintu + asyAH
tgt_word :	kintvasyAH
preds_word :	Ahaasmad
src_word :	AhaicCA + iti
tgt_word :	AhaicCeti
preds_word :	Ahaasmad
src_word :	yadA + aham
tgt_word :	yadAha

src_word :	viSezyABAvAt + asADAraRe
tgt_word :	viSezyABAvAdasADAraRe
preds_word :	yAtAyAdfSae
src_word :	nizWAparaH + alubDaH
tgt_word :	nizWAparo'lubDaH
preds_word :	kimanvizIyaM
src_word :	uktaH +
tgt_word :	ukto
preds_word :	viSezaRaM
src_word :	Adyakartavyam + AsIt
tgt_word :	AdyakartavyamAsIt
preds_word :	sarve'pi M_prAp
src_word :	iti + Alocayan
tgt_word :	ityAlocayan
preds_word :	ityapfcCat
src_word :	hAm + SivamUrttaye
tgt_word :	hAM_SivamUrttaye
preds_word :	kimanvizM
src_word :	iti + arTaH
tgt_word :	ityarTaH
preds_word :	ityuktvA
src_word :	yattfRAcCAditaSAlA + aDunA
tgt_word :	yattfRAcCAditaSAlA'DunA
preds_word :	rAjaputrA_Asan mAcakAra o_vartate
src_word :	pratiyogitvAdeH + anyasaMbaMDatvABAvAt
tgt_word :	pratiyogitvAderanyasaMbaMDatvABAvAt
preds_word :	idamupagamya M_jahASo'DyAyaH
src_word :	na + atidUravartinI
tgt_word :	nA'tidUravartinI
preds_word :	nApattiH
src_word :	jIrRANgAH + eva
tgt_word :	jIrRANgA_eva
preds_word :	ekazazwitamo'DyAyaH
src_word :	BArgavam + yajet
t

src_word :	api + aBUvan
tgt_word :	apyaBUvan
preds_word :	AhayaM
src_word :	rOdraH + aTa
tgt_word :	rOdro'Ta
preds_word :	dAnAvATa
src_word :	tAdfSasidDatvavyApyatvAt + iti
tgt_word :	tAdfSasidDatvavyApyatvAditi
preds_word :	tAdfSAnvayaboDaM_prati
src_word :	bahiH + AjagAma
tgt_word :	bahirAjagAma
preds_word :	punaryuva
src_word :	parasparam + paramA
tgt_word :	parasparaM_paramA
preds_word :	punaryuva
src_word :	Bojanam + AnIya
tgt_word :	BojanamAnIya
preds_word :	svaputraM_prAptavAn
src_word :	prasuptaH + AsIt
tgt_word :	prasupta_AsIt
preds_word :	pramatoktaH
src_word :	namaH + astu
tgt_word :	namo'stu
preds_word :	mAstu
src_word :	kramavatAm + iti
tgt_word :	kramavatAmiti
preds_word :	A_miti
src_word :	praDAnaH + jAtaH
tgt_word :	praDAno_jAtaH
preds_word :	praTEva
src_word :	tAdfSa + anuBavavizayaH
tgt_word :	tAdfSAnuBavavizayaH
preds_word :	tAdfSAnvayaboD
src_word :	aTa + uBayoH
tgt_word :	aToBayoH
preds_word :	kimetat
src_word :	SironABipAdAn + catasraH
tgt_word :	SironABipAdAMScat

src_word :	hAnam + ucyate
tgt_word :	hAnamucyate
preds_word :	hrIM_M_nAma
src_word :	Bavet + taTA
tgt_word :	BavettaTA
preds_word :	kadAcid
src_word :	prayuYjIta + eva
tgt_word :	prayuYjItEva
preds_word :	prayuqyAnetyAdi
src_word :	darBEH + catuzpaTam
tgt_word :	darBEScatuzpaTam
preds_word :	jahAM_prApityatrAo_mahAn
src_word :	DArayet + pUraRaM
tgt_word :	DArayetpUraRaM
preds_word :	tAmaSM
src_word :	patram + ekam
tgt_word :	patramekaM
preds_word :	sarvamidaM
src_word :	IdfSe + avasare
tgt_word :	IdfSe'vasare
preds_word :	viSezaRamitirItyA
src_word :	nakzatiH + itiDyeyam
tgt_word :	nakzatiritiDyeyam
preds_word :	evaM_namokzaryaM_kftvA
src_word :	praTamAtve + api
tgt_word :	praTamAtvepi
preds_word :	taTAhIti
src_word :	kiYcit + kAlAnantaraM
tgt_word :	kiYcitkAlAnantaraM
preds_word :	punaryuva
src_word :	Bojanam + karoti
tgt_word :	BojanaM_karoti
preds_word :	svaputra
src_word :	pratibaDyapratibanDakaBAvavfdDiH + iti
tgt_word :	pratibaDyapratibanDakaBAvavfdDiriti
preds_word :	kimanvizBAv

src_word :	praTamAyAH + tatrABAvena
tgt_word :	praTamAyAstatrABAvena
preds_word :	kimetat
src_word :	SvetaH + rasO
tgt_word :	Sveto_rasO
preds_word :	Ahaasmadlaviva
src_word :	svABAvaH + ca
tgt_word :	svABAvaSca
preds_word :	svAM_Sca
src_word :	na + asti
tgt_word :	nAsti
preds_word :	nAsti
src_word :	muniH + ekaH
tgt_word :	munireko
preds_word :	satyamasmi
src_word :	nizkAraRam + ekaM
tgt_word :	nizkAraRamekaM
preds_word :	idamupagamya
src_word :	na + anyat
tgt_word :	nAnyat
preds_word :	nApattiH
src_word :	jalAQakasupUrAH + tu
tgt_word :	jalAQakasupUrAstu
preds_word :	jahAkazAkazAstu
src_word :	nArakasya + iva
tgt_word :	nArakasyeva
preds_word :	kimetat
src_word :	prakftyarTam + eva
tgt_word :	prakftyarTameva
preds_word :	punaryuvaya_eva
src_word :	prAcInavicArAt + na
tgt_word :	prAcInavicArAnna
preds_word :	namonamoo_na
src_word :	tftIyaH + aDyAyaH
tgt_word :	tftiyo'DyAyaH
preds_word :	kimetat
src_word :	kaTam + aBUt
tgt_word :	kaTamaBUt
preds_word :	kaTamenaM
src_word :	apamAnam + a

...

src_word :	tat + na
tgt_word :	tanna
preds_word :	tatna
src_word :	saMSayahetuH + iti
tgt_word :	saMSayaheturiti
preds_word :	kimiti
src_word :	saH + tu
tgt_word :	sa_tu
preds_word :	sa_tu
src_word :	karmapariRAmaH + tu
tgt_word :	karmapariRAmastu
preds_word :	putrasneha
src_word :	na + AsIt
tgt_word :	nAsIt
preds_word :	nA
src_word :	Binna + evasvIkartavyA
tgt_word :	BinnEvasvIkartavyA
preds_word :	nADikaM
src_word :	prARarakzArTam + prayatate
tgt_word :	prARarakzArTaM_prayatate
preds_word :	hetutvAvacCinnABAvasya
src_word :	saH + vidvAn
tgt_word :	sa_vidvAn
preds_word :	sa_uvAca
src_word :	cezwAm + prati
tgt_word :	cezwAM_prati
preds_word :	svarUpAM_nAma
src_word :	kim + anyat
tgt_word :	kimanyat
preds_word :	kiM_nu
src_word :	tadanantaram + eva
tgt_word :	tadanantarameva
preds_word :	tadEva
src_word :	viBIzaRaHyad + AjYApayati
tgt_word :	viBIzaRaHyadAjYApayati
preds_word :	vilasitavyAH
src_word :	aBagnanAsikaH + ca
tgt_word :	aBagnanAsikaSca
preds_word :	aayamayAneSca
src_word :	na 

src_word :	tvat + mate
tgt_word :	tvanmate
preds_word :	triMSa
src_word :	saMSayasya + api
tgt_word :	saMSayasyApi
preds_word :	yaTA
src_word :	dakziRe + aTa
tgt_word :	dakziRe'Ta
preds_word :	sa_Re'Ta
src_word :	nirUpita + eva
tgt_word :	nirUpitEva
preds_word :	samakzamAR
src_word :	itTam + ca
tgt_word :	itTaM_ca
preds_word :	punaryuva
src_word :	jagaddevaH + tA
tgt_word :	jagaddevastA
preds_word :	samAanaM_tatra
src_word :	BUtAnAm + drazwA
tgt_word :	BUtAnAM_drazwA
preds_word :	idamupalakzaRam
src_word :	parABavan + iva
tgt_word :	parABavanniva
preds_word :	parADa: o_nAma
src_word :	pacati + ityAdO
tgt_word :	pacatItyAdO
preds_word :	tasmAdapi
src_word :	kadAcit + api
tgt_word :	kadAcidapi
preds_word :	kadAcidapi
src_word :	na + avartata
tgt_word :	nAvartata
preds_word :	nASaknot
src_word :	pARineH + AcAryasya
tgt_word :	pARinerAcAryasya
preds_word :	pAvakAkinrvA
src_word :	ca + asya
tgt_word :	cA'sya
preds_word :	cAsya
src_word :	awavIm + ullaNGya
tgt_word :	awavImullaNGya
preds_wor

src_word :	lipyakzarARAm + api
tgt_word :	lipyakzarARAmapi
preds_word :	kumArarAdavamapi
src_word :	nipAtAtirikte + ityarTaH
tgt_word :	nipAtAtiriktetyarTaH
preds_word :	tApaM_BAvAnna
src_word :	strIRAm + AryasvaBAvAnAm
tgt_word :	strIRAmAryasvaBAvAnAM
preds_word :	idamupalakzaRam
src_word :	SUrpaRaKA + AyAtA
tgt_word :	SUrpaRaKAyAtA
preds_word :	mAdavamaSAnaNgIkArAt
src_word :	devam + brahmaraTAdinA
tgt_word :	devaM_brahmaraTAdinA
preds_word :	satmaSCA
src_word :	samAyAtA + asmi
tgt_word :	samAyAtA'smi
preds_word :	samAyAneto
src_word :	SAbdaH + api
tgt_word :	SAbdo'pi
preds_word :	punaryuva
src_word :	pravAdam + kutaH
tgt_word :	pravAdaM_kutaH
preds_word :	pravAraM_da_uvAca vApramatasyE
src_word :	kecittu + iti
tgt_word :	kecittviti
preds_word :	ata_eva tyemiti
src_word :	SESavam + munibAlakE:
tgt_word :	SESavaM_munibAlakE:
preds_word :	SakumAracakAra
src_word :	kzubDavacAMsi + AkarRya
tgt_word :	kzubDavacAMsyAkarRya
preds_word :	viSezaRamitirItyA vakA'Beda
src_word :	iti + anubanDac

src_word :	zaw + ityucyante
tgt_word :	zaqityucyante
preds_word :	svarUpAM_prAptavAn
src_word :	tadBAsate + iti
tgt_word :	tadBAsata_iti
preds_word :	tadAdiSabd
src_word :	tadbADatvena + eva
tgt_word :	tadbADatvenEva
preds_word :	tadanupadameva
src_word :	na + avagataM
tgt_word :	nAvagataM
preds_word :	nAvasare
src_word :	sAkAMkzatvagrahayoH + ekatarasatve
tgt_word :	sAkAMkzatvagrahayorekatarasatve
preds_word :	sAhasto_BIteryaM_rAdarasti rityAdiboDaH rityAdi
src_word :	DAtoH + eva
tgt_word :	DAtoreva
preds_word :	punaryuva
src_word :	sUryAdiH + tatra
tgt_word :	sUryAdistatra
preds_word :	etaddeSavATa
src_word :	pakzaH + balavAn
tgt_word :	pakzo_balavAn
preds_word :	kaTaM_sADanam
src_word :	arTaH + avabudDa:
tgt_word :	arTo'vabudDa:
preds_word :	sa_vaYcava:
src_word :	glAniH + mArutamUQatA
tgt_word :	glAnirmArutamUQatA
preds_word :	SaryaM_dadAtacCamavadat
src_word :	vfdDEH + amAtyEH
tgt_word :	vfdDEramAtyEH
preds_word :	samamapaSyatItyAdO
src_word :	Danam +
tgt_word :	DanaM
preds_word :

src_word :	bahutvam + eveti
tgt_word :	bahutvameveti
preds_word :	tatkzaRaM_nAma
src_word :	pratyakzAt + ityarTaH
tgt_word :	pratyakzAdItyarTaH
preds_word :	tadavasT
src_word :	kftavAn + ayam
tgt_word :	kftavAnayam
preds_word :	kimetat
src_word :	naca + iti
tgt_word :	naceti
preds_word :	kaTamiti
src_word :	ayam + tu
tgt_word :	ayaM_tu
preds_word :	ayamatu
src_word :	kftAH + aBUvan
tgt_word :	kftA_aBUvan
preds_word :	samADiyo_Bavati rityAdiboDaH rityAdi
src_word :	svarRadaDyakzatEH + reKAH
tgt_word :	svarRadaDyakzatE_reKAH
preds_word :	gotvamasmAkaM Baratra
src_word :	hetum + matsyAdirUpiRam
tgt_word :	hetuM_matsyAdirUpiRam
preds_word :	svarUpAmaBAvAnna
src_word :	prayojakam + iti
tgt_word :	prayojakamiti
preds_word :	kaTamiti
src_word :	BarataH + yena
tgt_word :	Barato_yena
preds_word :	BaM_nItvA
src_word :	puruzAH + yat
tgt_word :	puruzA_yat
preds_word :	pA_Asan
src_word :	samaBUt + ityAdi
tgt_word :	samaBUdityAdi
preds_word :	samakzamARA M_prApto_Bavet raM_
src_word :	kzubDaH + ayaM

In [85]:
inference(model, train_dataloader_inference, "train")

src_word :	ityatra + ityAdiH
tgt_word :	ityatretyAdiH
preds_word :	yadvitH
src_word :	sarvam + avadAtam
tgt_word :	sarvamavadAtam
preds_word :	sarvaTEva
src_word :	iti + avocat
tgt_word :	ityavocat
preds_word :	ityapfcCat
src_word :	inDanam + api
tgt_word :	inDanamapi
preds_word :	samastamapi
src_word :	Bavatu + iti
tgt_word :	Bavatviti
preds_word :	syAditi
src_word :	saH + mAnuzaH
tgt_word :	sa_mAnuzaH
preds_word :	sa_uvAca
src_word :	gaNgAyamunam + uttamam
tgt_word :	gaNgAyamunamuttamam
preds_word :	punaryuvaM_prAptavAn
src_word :	Gawadvayena + ityarTaH
tgt_word :	GawadvayenEtyarTaH
preds_word :	GawapadindriyasaMba
src_word :	tftIyaH + api
tgt_word :	tftIyo'pi
preds_word :	kimapi
src_word :	BAryAm + Ahvayat
tgt_word :	BAryAmAhvayat
preds_word :	gotvamaTa
src_word :	AGArO + AjyaBAgO
tgt_word :	AGArAvAjyaBAgO
preds_word :	AkasmirityAdimAcayaTa
src_word :	vfttiprayojyavizayatvopagamena + eva
tgt_word :	vfttiprayojyavizayatvopagamenEva
preds_word :	svarUpABAvAdayasmin_eva
src_word :	vAca

src_word :	bahiH + AnIta:
tgt_word :	bahirAnIta:
preds_word :	punaryuvarasti
src_word :	mfgaH + BUtvA
tgt_word :	mfgo_BUtvA
preds_word :	samADikaM
src_word :	pratiyogitAvacCedakaGawatvAdeH + Aropyatvena
tgt_word :	pratiyogitAvacCedakaGawatvAderAropyatvena
preds_word :	pUrvavadatvAnpuruza M_tatra
src_word :	kASmIrikasUryasUnuvAsudevaviracitAyAm + nyAyasArapadapaYcikAyAm
tgt_word :	kASmIrikasUryasUnuvAsudevaviracitAyAM_nyAyasArapadapaYcikAyAM
preds_word :	AharAzwra
src_word :	cOhAnavaMSIyaH + mahApratApI
tgt_word :	cOhAnavaMSIyo_mahApratApI
preds_word :	hrIM_M_jahAvAwikAvATa
src_word :	kim + pakzatAvacCedakam
tgt_word :	kiM_pakzatAvacCedakam
preds_word :	kiM_nu
src_word :	drazwum + icCAmi
tgt_word :	drazwumicCAmi
preds_word :	kimetat
src_word :	yadyapi + iti
tgt_word :	yadyapIti
preds_word :	sameti
src_word :	prayojakam + na
tgt_word :	prayojakaM_na
preds_word :	kaTaM_na
src_word :	tat + guroH
tgt_word :	tad_guroH
preds_word :	taduktam
src_word :	ca + aliKAma
tgt_word :	cAliKAma
preds_wo

src_word :	pramARam + ityAdO
tgt_word :	pramARamityAdO
preds_word :	syAditi
src_word :	mUlyam + aDikaM
tgt_word :	mUlyamaDikaM
preds_word :	BaM_prAptavAn
src_word :	dattam + AsIt
tgt_word :	dattamAsIt
preds_word :	svarUpA
src_word :	om + trelokyavikrAntAya
tgt_word :	oM_trelokyavikrAntAya
preds_word :	oM_hAm
src_word :	sam + aDikam
tgt_word :	samaDikam
preds_word :	samakzamARetadAkarRya M_prAp
src_word :	vadDozRISAH + ca
tgt_word :	vadDozRISASca
preds_word :	vakA'gniSca
src_word :	mUrti:sA + eva
tgt_word :	mUrti:sEva
preds_word :	nanvanurikA
src_word :	evam + candra
tgt_word :	evaM_candra
preds_word :	evamapekzate
src_word :	bahman + asya
tgt_word :	bahmannasya
preds_word :	samamavadat
src_word :	kzipram + dravyARi
tgt_word :	kzipraM_dravyARi
preds_word :	pramatpraM_Bayatra
src_word :	purovAtA''taparajaH + tuzAraparuzA'nilAn
tgt_word :	purovAtA''taparajastuzAraparuzA'nilAn
preds_word :	svarUpAtaramamaSAnamaSraBinayaM
src_word :	raktam + api
tgt_word :	raktamapi
preds_word :	ramapi
src_

src_word :	SrAvakAH + yaTASakti
tgt_word :	SrAvakA_yaTASakti
preds_word :	AhaasmadlaBayatra
src_word :	muDA + eva
tgt_word :	muDEva
preds_word :	mumeva
src_word :	anena + asuranASena
tgt_word :	anenAsuranASena
preds_word :	sarvaTraBimAnA
src_word :	aprAmARikatvAt + iti
tgt_word :	aprAmARikatvAditi
preds_word :	apfzwo__iti
src_word :	kiYcit + arTakAmaBogopetaH
tgt_word :	kiYcidarTakAmaBogopetaH
preds_word :	punaryuvaM_prAptavAn
src_word :	agniH + uvAca
tgt_word :	agniruvAca
preds_word :	punaryuva
src_word :	vidyAtattvam + ca
tgt_word :	vidyAtattvaYca
preds_word :	tatkzaRaM_Sca
src_word :	tat + AkarRya
tgt_word :	tadAkarRya
preds_word :	tatayA
src_word :	kAcit + hAni:
tgt_word :	kAcidDAni:
preds_word :	kAMS:
src_word :	madIyAm + api
tgt_word :	madIyAmapi
preds_word :	idamapi
src_word :	niratAH + taTEva
tgt_word :	niratAstaTEva
preds_word :	nirUmaSo'DyAyaH
src_word :	iti + apekzAyAM
tgt_word :	ityapekzAyAM
preds_word :	ityapfcCat
src_word :	kim + anyat
tgt_word :	kimanyat
preds_word :	kiM

src_word :	tatra + upetya
tgt_word :	tatropetya
preds_word :	tatrAyam
src_word :	tasyAH + aSrubindavaH
tgt_word :	tasyA_aSrubindavo
preds_word :	tasyA_hfdayam mapekztamAsIt
src_word :	kuSAn + taTA
tgt_word :	kuSAMstaTA
preds_word :	kumArabDa
src_word :	idAnIm + dAsyAH
tgt_word :	idAnIM_dAsyAH
preds_word :	idAnIM_ja
src_word :	svAhA + iti
tgt_word :	svAheti
preds_word :	svAM__iti
src_word :	kupitaH + BUtvA
tgt_word :	kupito_BUtvA
preds_word :	eka_Asan
src_word :	sasarja + AdO
tgt_word :	sasarjAdO
preds_word :	salakazADa
src_word :	sTApatyakalAyAH + apratimaM
tgt_word :	sTApatyakalAyA_apratimaM
preds_word :	saMBaveyadimamenaM
src_word :	vayam + dehalyA:
tgt_word :	vayaM_dehalyA
preds_word :	vaMSaM_prAp
src_word :	SatayojanAyatam + aDvAnaM
tgt_word :	SatayojanAyatamaDvAnaM
preds_word :	taTAhIti
src_word :	caturTam + avaSezayet
tgt_word :	caturTamavaSezayet
preds_word :	idamupagamya
src_word :	upasaMKyAnama + ityapi
tgt_word :	upasaMKyAnamityapi
preds_word :	vizwasnaBas
src_word :	hi + eza

...

src_word :	saH + grAmIRaH
tgt_word :	sa_grAmIRaH
preds_word :	sa_vaYcayAmi
src_word :	tadanityam +
tgt_word :	tadanityaM
preds_word :	tadanupapannam
src_word :	raktEH + veRukaqiRqimEH
tgt_word :	raktErveRukaqiRqimEH
preds_word :	kimanvizIyaM_janyAnumityAdiyajati
src_word :	param + Sivam
tgt_word :	paraM_Sivam
preds_word :	paraM_etat
src_word :	rahasi + apfcCat
tgt_word :	rahasyapfcCat
preds_word :	yaTArTadaRqaH
src_word :	gamanAya + udyata:
tgt_word :	gamanAyodyata:
preds_word :	sa_kiman:
src_word :	pUrRam + AdAya
tgt_word :	pUrRamAdAya
preds_word :	satvenA
src_word :	mallaH + vijayanagare
tgt_word :	mallo_vijayanagare
preds_word :	yaTArTakatvopayAgaganDena naBasriMSo'DyAyaH M_
src_word :	Kalu + etat
tgt_word :	Kalvetat
preds_word :	Kalannapi
src_word :	sADAraRe + avyAptiH
tgt_word :	sADAraRe'vyAptiH
preds_word :	kimetat
src_word :	tat + SrutvA
tgt_word :	tacCrutvA
preds_word :	tacca
src_word :	tat + tu
tgt_word :	tattu
preds_word :	tattu
src_word :	vfdvaH + tu
tgt_word :	vfdvastu
pred

src_word :	prANgaRam + idaM
tgt_word :	prANgaRamidaM
preds_word :	prAsAdM_prAp
src_word :	dattaH + asti
tgt_word :	datto'sti
preds_word :	samakzasti
src_word :	ayam + aBisanDiH
tgt_word :	ayamaBisanDiH
preds_word :	ayamasti
src_word :	rAGavaH + rAjA
tgt_word :	rAGavo_rAjA
preds_word :	viSezaRamitirItyA
src_word :	etAvat + uktvA
tgt_word :	etAvaduktvA
preds_word :	punaryuvaM_nAma
src_word :	vIramatim + prAha
tgt_word :	vIramatiM_prAha
preds_word :	kimetat
src_word :	na + avaSizyate
tgt_word :	nAvaSizyate
preds_word :	nAvasare
src_word :	tAdfSaBAvatvena + aparA
tgt_word :	tAdfSaBAvatvenA'parA
preds_word :	tAdfSavAkyajanyaprasidDiH
src_word :	kAryatvAt + iti
tgt_word :	kAryatvAditi
preds_word :	sarvamiti
src_word :	asmin + nagare
tgt_word :	asminnagare
preds_word :	tApaM_o_mahAkazwavAwikAM_parir
src_word :	tatra + ativyAptiSaMkAyA
tgt_word :	tatrAtivyAptiSaMkAyA
preds_word :	tatrAM
src_word :	gataH + ahaM
tgt_word :	gato'haM
preds_word :	tvamas
src_word :	kaScit + anucaraH
tgt_word :	kaSc

src_word :	yAm + azwANgahfdayasaMhitAyAM
tgt_word :	yAmazwANgahfdayasaMhitAyAM
preds_word :	yAM_pratyakzAyaM_kftvA
src_word :	param +
tgt_word :	paraM
preds_word :	paraM_
src_word :	muKAgniH + datta:
tgt_word :	muKagnirdatta:
preds_word :	A_A_A'nyadA
src_word :	asmin + pakze
tgt_word :	asminpakze
preds_word :	asyEkasya
src_word :	vaktum + na
tgt_word :	vaktuM_na
preds_word :	cenna
src_word :	mftA + iva
tgt_word :	mfteva
preds_word :	go
src_word :	vidvAMsaH + aBUvan
tgt_word :	vidvAMso'BUvan
preds_word :	samvAsa_taM
src_word :	praSaMsApAtraH + baBUva
tgt_word :	praSaMsApAtro_baBUva
preds_word :	sAhasurjunasya AdAraBya nopasTitiH
src_word :	sEnyam + avalokya
tgt_word :	sEnyamavalokya
preds_word :	kimetat yaM_kftvA
src_word :	svArTAnvayapratiyogilakzyArTAnuBavam + prati
tgt_word :	svArTAnvayapratiyogilakzyArTAnuBavaM_prati
preds_word :	AhayAnetyAdihrIM_M_tatra
src_word :	taTAkalpanAt + na
tgt_word :	taTAkalpanAnna
preds_word :	taTAna
src_word :	saH + dadO
tgt_word :	sa_dadO
preds_word :	s

src_word :	devadUtaH + asi
tgt_word :	devadUto'si
preds_word :	taramasO M_prAp
src_word :	kaH + asO
tgt_word :	ko'sO
preds_word :	ko_nu
src_word :	na + AsIt
tgt_word :	nAsIt
preds_word :	nA
src_word :	bADitavAn + iti
tgt_word :	bADitavAniti
preds_word :	sa_vaYcayAmi
src_word :	tasmin + pramuKAH
tgt_word :	tasminpramuKAH
preds_word :	tasminneva
src_word :	gurUzRaH + anilahA
tgt_word :	gurUzRo'nilahA
preds_word :	hrIM_vABAvAdavasare
src_word :	paScAt + apaSyat
tgt_word :	paScAdapaSyat
preds_word :	syAditi
src_word :	puzpAdinizWaganDagrahaRatAtparyeRa + eva
tgt_word :	puzpAdinizWaganDagrahaRatAtparyeREva
preds_word :	ahamadya etadAkarRya mayyAmameva
src_word :	daSa + eva
tgt_word :	daSEva
preds_word :	tan_eva
src_word :	SarIrajanyatvam +
tgt_word :	SarIrajanyatvaM
preds_word :	svarUpA
src_word :	viSezaRam + na
tgt_word :	viSezaRaM_na
preds_word :	viSezaRaM_na
src_word :	svAduH + daSAmlaH
tgt_word :	svAdurdaSAmlaH
preds_word :	KalanAdAraBya
src_word :	daDilepaSabalam + ca
tgt_word :	daDile

KeyboardInterrupt: 

In [87]:
def calcAcc(filename):
    with open(filename, "r") as fread:
        lines = fread.readlines()
    total_counter = 0
    matched_counter = 0
    tgt = ""
    preds = ""
    for line in lines:
        if(line.startswith("src_word :")):
            continue
        elif(line.startswith("tgt_word :")):
            tgt = line.split("\t")[1].split("\n")[0]
        elif(line.startswith("preds_word :")):
            preds = line.split("\t")[1].split("\n")[0]
            if(preds == tgt):
                matched_counter = matched_counter + 1
            total_counter = total_counter + 1
    print("{} : {}/{} || {}".format(filename, matched_counter, total_counter, (matched_counter/total_counter)*100))

In [89]:
calcAcc("output/test_output.txt")

output/test_output.txt : 613/16538 || 3.706615068327488


In [91]:
calcAcc("output/train_output.txt")

output/train_output.txt : 1026/28975 || 3.540983606557377


In [ ]:
start = time.time()
current_datetime = datetime.now()
best_valid_data_loss = float('inf')
with open("logs/loss_log_"+str(current_datetime.year)+"_"+str(current_datetime.month)+"_"+str(current_datetime.day)+"_"+str(current_datetime.hour)+"_"+str(current_datetime.minute)+"_"+str(current_datetime.second)+".log", "w") as flogwrite:
    for epoch in range(epochs):
        model.train()
        total_loss = 0
        counter = 0
        for i, (src1, src2, tgt) in enumerate(valid_dataloader):
            src1 = src1.transpose(0, 1).cuda()
            src2 = src2.transpose(0, 1).cuda()
            tgt = tgt.transpose(0, 1).cuda()
            tgt_input = tgt[:, :-1].cuda()
#             print("src1[0] : {}".format(src1[0]))
#             print("src2[0] : {}".format(src2[0]))
#             print("tgt_input[0] : {}".format(tgt_input[0]))
#             print("src1.shape : {}".format(src1.shape))
#             print("src2.shape : {}".format(src2.shape))
#             print("tgt_input.shape : {}".format(tgt_input.shape))
            start_token = torch.from_numpy(np.array([joint_vocab_index_dict["<START>"]])).cuda()
            src = []
            index_list = []
            tgt_list = []
            for i in range(src1.size(0)):
                indexes = (src1[i] == joint_vocab_index_dict["<PAD>"]).nonzero(as_tuple=False)
                if(indexes.shape[0] == 0):
                    index_list.append(-1)
                    src.append(torch.cat([src1[i], src2[i]]))
                else:
                    index = indexes[0][0]
                    index_list.append(index)
                    src.append(torch.cat([src1[i, :index], src2[i], src1[i, index:]]))
                src[i] = src[i][:src1.size(1)]
                tgt_list.append(torch.cat([start_token, tgt_input[i, :]]))
            src = torch.stack(src).cuda()
            tgt_list_input = torch.stack(tgt_list).cuda()
            src_mask1, src_mask2, tgt_mask1, src_mask3 = getMasks(src1, src2, src, tgt_list_input)
#             src1 = src1.type(torch.LongTensor)
#             src2 = src2.type(torch.LongTensor)
#             tgt = tgt.type(torch.LongTensor)
#             print("tgt_list_input.shape : {}".format(tgt_list_input.shape))
#             print("src.shape : {}".format(src.shape))
#             print("tgt_mask1[0] : {}".format(tgt_mask1[0]))
#             print("src_mask1[0] : {}".format(src_mask1[0]))
#             print("src_mask2[0] : {}".format(src_mask2[0]))
#             print("src_mask3[0] : {}".format(src_mask3[0]))
            preds = model(src1, src2, tgt_list_input, src_mask1, src_mask2, tgt_mask1, src_mask3, index_list)
#             print("preds.shape : {}".format(preds.shape))
            ys = tgt[:, :].contiguous().view(-1)
            preds_just = preds.view(-1, preds.size(-1))
#             print("preds_just.shape : {}".format(preds_just.shape))
#             print("ys.shape : {}".format(ys.shape))
            optimizer.zero_grad()
            loss = F.cross_entropy(preds_just, ys, ignore_index=joint_vocab_index_dict["<PAD>"])
            loss.backward()
            optimizer.step()
            total_loss += loss.item()
            counter = counter + 1
            print("total time till : {} || epoch : {} || batch : {} || train loss : {}".format((time.time() - start)//60, epoch + 1, counter, loss.item()))
            flogwrite.write("total time till : {} || epoch : {} || batch : {} || train loss : {}\n".format((time.time() - start)//60, epoch + 1, counter, loss.item()))
        curr_valid_data_loss = prediction_loss(model, valid_dataloader)
        if(curr_valid_data_loss < best_valid_data_loss):
            torch.save(model.state_dict(), 'checkpoints/best_checkpoint.pt')
            best_valid_data_loss = curr_valid_data_loss
        if(epoch == 0):
            torch.save(model.state_dict(), 'checkpoints/'+str(epoch+1)+'.pt')
        else:
            os.remove("checkpoints/"+str(epoch)+".pt")
            torch.save(model.state_dict(), 'checkpoints/'+str(epoch+1)+'.pt')
        print("total time till : {} || epoch : {} || train loss : {} || valid loss : {}".format((time.time() - start)//60, epoch + 1, total_loss/counter, curr_valid_data_loss))
        flogwrite.write("total time till : {} || epoch : {} || train loss : {} || valid loss : {}\n".format((time.time() - start)//60, epoch + 1, total_loss/counter, curr_valid_data_loss))